# Displaying images in Python

In [69]:
import os 
from astropy.io import fits
import numpy as np
import matplotlib.pyplot as plt

In [ ]:
path_in = '/Users/jmilli/Documents/these/Python/coffee/coffee_display_images'
image = fits.getdata(os.path.join(path_in,'outIm_resmean_mcadi_HR4796.fits'))

## Basic display

### Default display

In [70]:
plt.imshow(image,cmap='gray')
plt.show()

In [71]:
print(type(image.flat))

<type 'numpy.flatiter'>


In [72]:
NBINS = 1000
flattened_image = image.flat
histogram = plt.hist(flattened_image[np.isfinite(flattened_image)], NBINS,range=(-20,20))
plt.show()

In [73]:
plt.imshow(image, cmap='CMRmap',vmin=-50,vmax=300)
plt.show()

In [74]:
from matplotlib.colors import LogNorm
plt.imshow(image+100, cmap='gray', norm=LogNorm())
plt.show()

In [75]:
plt.imshow?

In [76]:
plt.imshow(image, cmap='CMRmap', origin='lower',vmin=-50,vmax=300)
plt.colorbar()
plt.show()

### With x and y axis in arcsec

In [77]:
fig, ax = plt.subplots()
im = ax.imshow(image, cmap='CMRmap', origin='lower',vmin=-50,vmax=300)
ny,nx=image.shape
px_scale = 0.01225
im.set_extent(np.array([-nx/2,nx/2-1,-nx/2,nx/2-1])*px_scale)
ax.text(-1.0,2.0,'HR 4796 A',color='white',fontsize=25)
plt.xlabel('Distance in arcsec')
plt.ylabel('Distance in arcsec')
plt.show()

## Interfacing SAO Image DS9

### Importing an image from DS9 to python

In [78]:
import pyds9

In [79]:
ds9 = pyds9.DS9()

In [80]:
ds9?

In [81]:
image_ds9 = ds9.get_arr2np()

In [83]:
plt.imshow(image_ds9, cmap='CMRmap', origin='lower')#,vmin=-50,vmax=300)
plt.colorbar()
plt.show()

### Importing an image from python to DS9

In [84]:
image2 = fits.getdata(os.path.join(path_in,'outIm_resmean_cadi_bPic.fits'))
ds9.set_np2arr(image2)

1

In [85]:
import cv2
unsharp_masked_image = image2 - cv2.medianBlur(image2.astype(np.float32),5)
ds9.set_np2arr(unsharp_masked_image)

1

### Setting regions

In [86]:
ds9.set_np2arr(image)
ds9.set('regions','circle({0:5.2f},{1:5.2f},{2:5.2f}) # color=yellow width=2 text={{{3:s}}}'.format(nx/2+1,nx/2+1,1./px_scale,'Circle of 1 arcsec radius'))

1

In [87]:
airy_minimum_m = np.array([1.22,2.23,3.24,4.24,5.24,6.24,7.25,8.25,9.25,10.25])
airy_maximum_m = np.array([ 0  ,1.64,2.68,3.70,4.71,5.72,6.72,7.73,8.73,9.73 ])
lam=1.6e-6
D=8.
fwhm = np.rad2deg(lam/D)*3600/px_scale
print(fwhm)
airy_maximum_px = airy_maximum_m*fwhm
airy_minimum_px = airy_minimum_m*fwhm

3.36758867342


In [88]:
ds9.set_np2arr(image)
for airy_maximum in airy_maximum_px:
    ds9.set('regions','circle({0:5.2f},{1:5.2f},{2:5.2f}) # color=yellow width=2'.format(nx/2+1,nx/2+1,airy_maximum))
for airy_minimum in airy_minimum_px:
    ds9.set('regions','circle({0:5.2f},{1:5.2f},{2:5.2f}) # color=black width=2'.format(nx/2+1,nx/2+1,airy_minimum))

### Getting regions

In [89]:
region=ds9.get("regions")
print(region)

# Region file format: DS9 version 4.1
global color=green dashlist=8 3 width=1 font="helvetica 10 normal roman" select=1 highlite=1 dash=0 fixed=0 edit=1 move=1 delete=1 include=1 source=1
physical
circle(215.86947,138.3071,5.2875072)



In [90]:
import pyregion
parsedRegion = pyregion.parse(region)
print parsedRegion

[Shape : circle ( Number(215.86947),Number(138.3071),Number(5.2875072) )]


In [91]:
parsedRegion[0]

Shape : circle ( Number(215.86947),Number(138.3071),Number(5.2875072) )

In [92]:
parsedRegion[0].name

'circle'

In [93]:
parsedRegion[0].coord_list

[215.86947, 138.3071, 5.2875072]

In [96]:
parsedRegion[0].comment

## Creating masks for spatial filtering

In [97]:
region=ds9.get("regions")
hdulist = fits.open(os.path.join(path_in, 'outIm_restmean_cadi_left.fits'))
h = hdulist[0].header
hdulist.close()

parsedRegion = pyregion.parse(region).as_imagecoord(h)

In [98]:
print parsedRegion

[Shape : ellipse ( Number(201.80376),Number(196.17747),Number(110),Number(25),Number(117) ), Shape : ellipse ( Number(201.80376),Number(196.17747),Number(74.347351),Number(14),Number(117) )]


In [99]:
myfilter = parsedRegion.get_filter()
mask_ellipse = (~myfilter[1] & myfilter[0]).mask((ny,nx))

In [101]:
type(mask_ellipse)


numpy.ndarray

In [102]:
mask_ellipse.shape

(400, 400)

In [103]:
ds9.set_np2arr(mask_ellipse*1.)

1

In [104]:
ds9.set_np2arr(mask_ellipse*image)

1

In [105]:
ds9.set_np2arr((1-mask_ellipse)*image)

1

For more information: http://pyregion.readthedocs.org/en/latest/users/overview.html

RO.DS9 is an alternative to interface Python with DS9. It seems to handle cubes of images as well.

